#### Check pictures in SPA och söka i SPA med folk kopplade till IFK Göteborg
* [This notebook](https://github.com/salgo60/spa2Commons/blob/main/Notebook/SPA%20IFKDB.ipynb) *
* IFK Göteborg
  * [ifkdb.se](https://ifkdb.se)
  * Wikidata [property P11905](https://www.wikidata.org/wiki/Property:P11905)
      * GITHUB Issue [#12](https://github.com/salgo60/ifkdb/issues/12)
      * API SPA https://portrattarkiv.se/endpoints/search.php
      * [SPARQL söker fram gubbar i WD födda innan 1920](https://w.wiki/7Ayd)

In [1]:
from datetime import datetime
start_time  = datetime.now()
print("Last run: ", start_time)

Last run:  2023-08-05 09:33:38.493497


In [2]:
import urllib3, json
import pandas as pd 
http = urllib3.PoolManager() 

url= "https://portrattarkiv.se/endpoints/search.php"  


In [3]:


import sys
from SPARQLWrapper import SPARQLWrapper, JSON

endpoint_url = "https://query.wikidata.org/sparql"

# IFKDB personer födda innan 1920 utan bild - SPA innehåller mest gamla personer
queryIFKDB = """SELECT (CONCAT (?itemLabel," ",str(year(?birthDate))) AS ?search) ?item ?itemLabel 
  (str(year(?birthDate)) AS ?year)
  WHERE {
  ?item wdt:P11905 ?ifkdb. 
  minus{?item wdt:P19 ?img}
  ?item wdt:P569 ?birthDate. 
  FILTER(xsd:integer(year(?birthDate)) < 1920)
  SERVICE wikibase:label { bd:serviceParam wikibase:language "sv", "en". }
} order by ?itemLabel """


 
def get_sparql_dataframe(endpoint_url, query):
    """
    Helper function to convert SPARQL results into a Pandas data frame.
    """
    user_agent = "salgo60/%s.%s" % (sys.version_info[0], sys.version_info[1])
 
    sparql = SPARQLWrapper(endpoint_url, agent=user_agent)
    sparql.setQuery(query)
    sparql.setReturnFormat(JSON)
    result = sparql.query()

    processed_results = json.load(result.response)
    cols = processed_results['head']['vars']

    out = []
    for row in processed_results['results']['bindings']:
        item = []
        for c in cols:
            item.append(row.get(c, {}).get('value'))
        out.append(item)

    return pd.DataFrame(out, columns=cols)

#SPAdf = get_sparql_dataframe(endpoint_url, query)
#SPAdf = get_sparql_dataframe(endpoint_url, queryNoPicNorra1890)
SPAdf = get_sparql_dataframe(endpoint_url, queryIFKDB)

SPAdf.info()   

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 34 entries, 0 to 33
Data columns (total 4 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   search     34 non-null     object
 1   item       34 non-null     object
 2   itemLabel  34 non-null     object
 3   year       34 non-null     object
dtypes: object(4)
memory usage: 1.2+ KB


In [4]:
  SPAdf

search                                       item  \
0             Algot Bengtsson 1900  http://www.wikidata.org/entity/Q121160719   
1             Algot Bergström 1909  http://www.wikidata.org/entity/Q121160723   
2              Algot Carlsson 1901  http://www.wikidata.org/entity/Q121160727   
3              Arne Göransson 1918  http://www.wikidata.org/entity/Q121160739   
4                 Bertil Gren 1918  http://www.wikidata.org/entity/Q121160738   
5                   Bror Berg 1917  http://www.wikidata.org/entity/Q121160720   
6               Douglas Krook 1897    http://www.wikidata.org/entity/Q1252363   
7                  Einar Haak 1901  http://www.wikidata.org/entity/Q121160740   
8             Elis Berndtsson 1902  http://www.wikidata.org/entity/Q121160724   
9              Emil Davidsson 1883  http://www.wikidata.org/entity/Q121160729   
10             Erik Dahlström 1889  http://www.wikidata.org/entity/Q121160728   
11              Erik Eiserman 1892  http://www.wikidata.org/entity/Q121160732   
12          Franklin Edenholm 1891  http://www.wikidata.org/entity/Q121160731   
13                 Georg Borg 1913  http://www.wikidata.org/entity/Q121160726   
14  Gillis Gillås (Andersson) 1895  http://www.wikidata.org/entity/Q121160712   
15            Gunnar Arcadius 1891  http://www.wikidata.org/entity/Q121160717   
16            Gunnar Forsberg 1911  http://www.wikidata.org/entity/Q121160735   
17          Gustaf Hermansson 1900  http://www.wikidata.org/entity/Q121160746   
18               Gösta Bohman 1911  http://www.wikidata.org/entity/Q121160725   
19             Göte Andersson 1919  http://www.wikidata.org/entity/Q121160713   
20             Harry Bergelin 1890  http://www.wikidata.org/entity/Q121160721   
21            Helge Andersson 1899  http://www.wikidata.org/entity/Q121160714   
22             John Andersson 1914  http://www.wikidata.org/entity/Q121160715   
23             John Hellström 1898  http://www.wikidata.org/entity/Q121160745   
24              John Säwström 1886  http://www.wikidata.org/entity/Q121052611   
25         Karl-Erik Eliasson 1916  http://www.wikidata.org/entity/Q121160733   
26                 Olof Hjärn 1903  http://www.wikidata.org/entity/Q121160747   
27               Ove Erickson 1884  http://www.wikidata.org/entity/Q121160734   
28                  Per Frise 1893  http://www.wikidata.org/entity/Q121160737   
29         Torsten Augustsson 1901  http://www.wikidata.org/entity/Q121160718   
30                Uno Bergman 1911  http://www.wikidata.org/entity/Q121160722   
31           Vallentin Hultén 1911  http://www.wikidata.org/entity/Q121160750   
32             Viktor Hansson 1893  http://www.wikidata.org/entity/Q121160742   
33              Yngve Hedelin 1909  http://www.wikidata.org/entity/Q121160743   

                    itemLabel  year  
0             Algot Bengtsson  1900  
1             Algot Bergström  1909  
2              Algot Carlsson  1901  
3              Arne Göransson  1918  
4                 Bertil Gren  1918  
5                   Bror Berg  1917  
6               Douglas Krook  1897  
7                  Einar Haak  1901  
8             Elis Berndtsson  1902  
9              Emil Davidsson  1883  
10             Erik Dahlström  1889  
11              Erik Eiserman  1892  
12          Franklin Edenholm  1891  
13                 Georg Borg  1913  
14  Gillis Gillås (Andersson)  1895  
15            Gunnar Arcadius  1891  
16            Gunnar Forsberg  1911  
17          Gustaf Hermansson  1900  
18               Gösta Bohman  1911  
19             Göte Andersson  1919  
20             Harry Bergelin  1890  
21            Helge Andersson  1899  
22             John Andersson  1914  
23             John Hellström  1898  
24              John Säwström  1886  
25         Karl-Erik Eliasson  1916  
26                 Olof Hjärn  1903  
27               Ove Erickson  1884  
28                  Per Frise  1893  
29         Torsten Augustsson  1901  
30            

In [5]:
SPAdetail = "https://portrattarkiv.se/details/"
for index, row  in SPAdf.iterrows():
    print("\n",row["search"],row["item"])
    encoded_body = json.dumps({
        "limit": "5",
        "from": "0",
        "birthyear":row["year"],
        "all":row["search"]
    })
    
    r = http.request('POST', url,
                 headers={'Content-Type': 'application/json'},
                 body=encoded_body)

    if r.status != 200:
        print(r.status)
        continue
    
    data = json.loads(r.data.decode('utf-8'),) 
    urls = []


    for h in data["hits"]["hits"]:
        id = h["_id"]
        #print(h)
        source = h["_source"]
        try:
 #           urlPicture = urlbasePic + id
 #           urls.append(urlPicture)
            score = h["_score"]
            FirstName = source["FirstName"]
            LastName = source["LastName"]
            BirthYear = source["BirthYear"]
            print("\t\t",score,FirstName, " ", LastName, " - ", BirthYear,SPAdetail+id, "\t", )
        except:
            print("Error")



 Algot Bengtsson 1900 http://www.wikidata.org/entity/Q121160719
		 15.94536 Algot   Fredriksson  -  1900 https://portrattarkiv.se/details/IQojCnw0WmAAAAAAAAA9OA 	
		 15.916247 Algot   Holmberg  -  1900 https://portrattarkiv.se/details/j6S8rJvx9lAAAAAAAACn7g 	
		 15.848149 Algot   Andersson  -  1900 https://portrattarkiv.se/details/sj9PGLAlnmUAAAAAAA5cZQ 	
		 15.777628 Algot   Bergström  -  1900 https://portrattarkiv.se/details/TNQaWo324IAAAAAAAADOgQ 	
		 15.600735 Algot   Fredriksson  -  1900 https://portrattarkiv.se/details/sj9PGLAlnmUAAAAAABa5vw 	

 Algot Bergström 1909 http://www.wikidata.org/entity/Q121160723
		 22.018814 Algot   Bergström  -  1909 https://portrattarkiv.se/details/TNQaWo324IAAAAAAAADOfw 	
		 16.598473 Algot   Sjölén  -  1909 https://portrattarkiv.se/details/sj9PGLAlnmUAAAAAABOyaQ 	
		 16.533447 Einar   Bergström  -  1909 https://portrattarkiv.se/details/TNQaWo324IAAAAAAAADO0Q 	
		 16.48222 Nils   Bergström  -  1909 https://portrattarkiv.se/details/TNQaWo324IAAAAAA

		 14.400093 Gunnar   Alm  -  1891 https://portrattarkiv.se/details/sj9PGLAlnmUAAAAAAB6rng 	
		 14.330535 Gunnar   Karlström  -  1891 https://portrattarkiv.se/details/0piq-fX0h5AAAAAAAAAsYQ 	
		 14.240623 Gunnar   Alm  -  1891 https://portrattarkiv.se/details/sj9PGLAlnmUAAAAAAA2C1A 	
		 14.125583 Gunnar   Wessman  -  1891 https://portrattarkiv.se/details/ciLMGSqrYjAAAAAAAAAqfQ 	
		 14.075785 Gunnar   Holmgren  -  1891 https://portrattarkiv.se/details/j6S8rJvx9lAAAAAAAABpRA 	

 Gunnar Forsberg 1911 http://www.wikidata.org/entity/Q121160735
		 18.6213 Gunnar   Eklund  -  1911 https://portrattarkiv.se/details/TR3yO_GV8eAAAAAAAABaqw 	
		 17.861698 Sivert   Forsberg  -  1911 https://portrattarkiv.se/details/IQojCnw0WmAAAAAAAAAfmg 	
		 17.572128 Sivert   Forsberg  -  1911 https://portrattarkiv.se/details/IQojCnw0WmAAAAAAAAAfmw 	
		 17.253124 Hilding   Forsberg  -  1911 https://portrattarkiv.se/details/IQojCnw0WmAAAAAAAABEYw 	
		 16.952282 Linus   Forsberg  -  1911 https://portrattarkiv.se/de

		 20.691498 Vivi-Anne   Hultén  -  1911 https://portrattarkiv.se/details/j6S8rJvx9lAAAAAAAAC3rQ 	
		 20.691498 Vivi-Anne   Hultén  -  1911 https://portrattarkiv.se/details/sj9PGLAlnmUAAAAAABO32A 	
		 20.670408 Gösta   Hultén  -  1911 https://portrattarkiv.se/details/seuNpYu6DKAAAAAAAAAK2A 	
		 20.375221 Vivi-Anne   Hultén  -  1911 https://portrattarkiv.se/details/sj9PGLAlnmUAAAAAACY1Aw 	
		 20.286041 Gösta   Hultén  -  1911 https://portrattarkiv.se/details/sj9PGLAlnmUAAAAAABVCiA 	

 Viktor Hansson 1893 http://www.wikidata.org/entity/Q121160742
		 21.232319 Viktor   Andersson-Hansson  -  1893 https://portrattarkiv.se/details/sj9PGLAlnmUAAAAAABFilg 	
		 16.6777 Viktor   Broman  -  1893 https://portrattarkiv.se/details/sj9PGLAlnmUAAAAAAA29rg 	
		 16.512064 Viktor   Karlström  -  1893 https://portrattarkiv.se/details/0piq-fX0h5AAAAAAAAAr4g 	
		 16.488897 Viktor   Jonsson  -  1893 https://portrattarkiv.se/details/Di4a42b6X_AAAAAAAABR7A 	
		 16.250143 Helga   Hansson  -  1893 https://portra